In [1]:
#from mpl_toolkits.basemap import Basemap, cm
import os.path
import os
import sys
from matplotlib import rcParams
from matplotlib.animation import ArtistAnimation
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

from datetime import datetime, timedelta
from siphon.cdmr import Dataset
import numpy as np
import numpy.ma as ma
import netCDF4

import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.io.shapereader import Reader
from cartopy.feature import ShapelyFeature
import cartopy.io.shapereader as shpreader

from siphon.catalog import TDSCatalog
from siphon.ncss import NCSS
import scipy.ndimage as ndimage
import scipy.signal as signal

from metpy.plots import StationPlot
from metpy.plots.wx_symbols import sky_cover
from metpy.calc import (bunkers_storm_motion, bulk_shear, dewpoint, dewpoint_from_relative_humidity, dry_lapse, moist_lapse,
                        vapor_pressure, saturation_vapor_pressure, wind_speed, wind_direction, pressure_to_height_std,
                        mixing_ratio, cape_cin, wind_components, height_to_pressure_std, equivalent_potential_temperature,
                        parcel_profile, precipitable_water, storm_relative_helicity, mean_pressure_weighted, 
                        most_unstable_cape_cin, most_unstable_parcel, supercell_composite, significant_tornado, get_layer,
                        relative_humidity_from_dewpoint, surface_based_cape_cin, mixed_layer_cape_cin, el, cape_cin,
                        surface_based_cape_cin, potential_temperature, wind_direction, add_pressure_to_height,
                        add_height_to_pressure, divergence, vorticity, lat_lon_grid_deltas, mixed_parcel,
                        most_unstable_parcel, lcl, lfc, mixing_ratio_from_relative_humidity, virtual_potential_temperature,
                        frontogenesis)

from metpy.units import units
from metpy.plots import SkewT
from metpy.plots import Hodograph
from metpy.interpolate import interpolate_1d as metinterp
from metpy.interpolate import log_interpolate_1d
from metpy.calc.tools import get_layer, get_layer_heights
from metpy.plots.declarative import (BarbPlot, ContourPlot, FilledContourPlot, MapPanel, PanelContainer, PlotObs)

import sharppy
import sharppy.sharptab.profile as profile
import sharppy.sharptab.interp as interp
import sharppy.sharptab.winds as winds
import sharppy.sharptab.utils as utils
import sharppy.sharptab.params as params
import sharppy.sharptab.thermo as thermo

import pickle
import csv
import pandas as pd
import xarray as xr
import math

In [2]:
#from notify_run import Notify
#notify = Notify()
#notify.register()
import matplotlib.patches as patches

In [3]:
from matplotlib.patches import Rectangle
import matplotlib.patches as mpatches

In [20]:
fig=plt.figure(figsize = (36, 36), dpi=400)
ax = plt.axes(projection=ccrs.PlateCarree())
#ax.imshow(SFCP[0])

reader = shpreader.Reader(r"D:/THESIS/Thesis GIS Data/County1010/countyl010g.shp")
counties = list(reader.geometries())
COUNTIES = cfeature.ShapelyFeature(counties, ccrs.PlateCarree())
proj = ccrs.PlateCarree()

ax.add_feature(cfeature.STATES.with_scale('50m'), linestyle='-', edgecolor='black', linewidth=1.75)
ax.add_feature(COUNTIES, facecolor='none', edgecolor='black', linewidth=1.5)

#ax.set_extent([-100.73, -91.36, 32.52, 39.10])
#ax.set_extent([-101.0, -93.0, 33.0, 38.0])
ax.set_extent([-100.25, -94.0, 32.85, 37.30])
#ax.set_extent([-100.25, -94.0, 33.0, 37.00])
#ax.set_extent([-100.73, -91.24, 31.9, 38.9])

#C:\Users\kyled\Desktop\ UNL MS Thesis/1 - Cell Tracking/Cell Tracking Map/TimeSplits

csv18_19 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/18_19.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv19_20 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/19_20.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv20_21 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/20_21_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv21_22 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/21_22_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv22_23 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/22_23_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv23_0 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/23_0_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv00_01 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/00_01_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv01_02 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/01_02_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv02_03 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/02_03.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv03_04 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/03_04.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv04_05 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/04_05.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv05_06 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/05_06.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv06_07 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/06_07.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv07_08 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/07_08.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])

# csv19_20_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/19_20_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv20_21_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/20_21_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv21_22_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/21_22_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv22_23_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/22_23_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv23_0_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/23_0_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv00_01_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/00_01_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv01_02_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/01_02_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv02_03_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/02_03_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv03_04_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/03_04_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv04_05_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/04_05_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv05_06_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/05_06_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv06_07_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/06_07_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
# csv07_08_120 = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/07_08_120min.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])

csv19_20_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/19_20_Supercell.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv20_21_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/20_21_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv21_22_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/21_22_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv22_23_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/22_23_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv23_0_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/23_0_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv00_01_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/00_01_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv01_02_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/01_02_Supercell30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv02_03_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/02_03_Supercell30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv03_04_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/03_04_Supercell30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv04_05_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/04_05_Supercell.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv05_06_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/05_06_Supercell.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv06_07_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/06_07_Supercell.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv07_08_Supercell = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/07_08_Supercell.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])

csv19_20_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/19_20_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv20_21_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/20_21_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv21_22_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/21_22_Severe30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv22_23_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/22_23_Severe30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv23_0_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/23_0_Severe30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv00_01_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/00_01_Severe30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv01_02_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/01_02_Severe30_ALLGROUPS.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv02_03_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/02_03_Severe30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv03_04_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/03_04_Severe30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv04_05_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/04_05_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv05_06_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/05_06_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv06_07_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/06_07_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv07_08_Severe = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/07_08_Severe.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])

csv19_20_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/19_20_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv20_21_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/20_21_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv21_22_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/21_22_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv22_23_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/22_23_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv23_0_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/23_0_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv00_01_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/00_01_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv01_02_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/01_02_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv02_03_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/02_03_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
csv03_04_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/03_04_Tornado30.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv04_05_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/04_05_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv05_06_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/05_06_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv06_07_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/06_07_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])
#csv07_08_Tornado = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/TimeSplits/07_08_Tornado.csv', usecols=['StormID', 'Start', 'End', 'Life (in mins)', 'Rounded Time (mins)', 'Demise', 'Radar', 'Ini_Lat', 'Ini_Lon', 'Ini_Time', 'Lat_2', 'Lon_2', 'Time_2'])


#for i in range(0, len(csv19_20['Ini_Lon'])):
x_values18 = [csv18_19['Ini_Lon'][:], csv18_19['Lon_2'][:]]
y_values18 = [csv18_19['Ini_Lat'][:], csv18_19['Lat_2'][:]]
x_values19 = [csv19_20['Ini_Lon'][:], csv19_20['Lon_2'][:]]
y_values19 = [csv19_20['Ini_Lat'][:], csv19_20['Lat_2'][:]]
x_values20 = [csv20_21['Ini_Lon'][:], csv20_21['Lon_2'][:]]
y_values20 = [csv20_21['Ini_Lat'][:], csv20_21['Lat_2'][:]]
x_values21 = [csv21_22['Ini_Lon'][:], csv21_22['Lon_2'][:]]
y_values21 = [csv21_22['Ini_Lat'][:], csv21_22['Lat_2'][:]]
x_values22 = [csv22_23['Ini_Lon'][:], csv22_23['Lon_2'][:]]
y_values22 = [csv22_23['Ini_Lat'][:], csv22_23['Lat_2'][:]]
x_values23 = [csv23_0['Ini_Lon'][:], csv23_0['Lon_2'][:]]
y_values23 = [csv23_0['Ini_Lat'][:], csv23_0['Lat_2'][:]]
x_values00 = [csv00_01['Ini_Lon'][:], csv00_01['Lon_2'][:]]
y_values00 = [csv00_01['Ini_Lat'][:], csv00_01['Lat_2'][:]]
x_values01 = [csv01_02['Ini_Lon'][:], csv01_02['Lon_2'][:]]
y_values01 = [csv01_02['Ini_Lat'][:], csv01_02['Lat_2'][:]]
x_values02 = [csv02_03['Ini_Lon'][:], csv02_03['Lon_2'][:]]
y_values02 = [csv02_03['Ini_Lat'][:], csv02_03['Lat_2'][:]]
x_values03 = [csv03_04['Ini_Lon'][:], csv03_04['Lon_2'][:]]
y_values03 = [csv03_04['Ini_Lat'][:], csv03_04['Lat_2'][:]]
# x_values04 = [csv04_05['Ini_Lon'][:], csv04_05['Lon_2'][:]]
# y_values04 = [csv04_05['Ini_Lat'][:], csv04_05['Lat_2'][:]]
# x_values05 = [csv05_06['Ini_Lon'][:], csv05_06['Lon_2'][:]]
# y_values05 = [csv05_06['Ini_Lat'][:], csv05_06['Lat_2'][:]]
# x_values06 = [csv06_07['Ini_Lon'][:], csv06_07['Lon_2'][:]]
# y_values06 = [csv06_07['Ini_Lat'][:], csv06_07['Lat_2'][:]]
# x_values07 = [csv07_08['Ini_Lon'][:], csv07_08['Lon_2'][:]]
# y_values07 = [csv07_08['Ini_Lat'][:], csv07_08['Lat_2'][:]]


# x_values19_120min = [csv19_20_120['Ini_Lon'][:], csv19_20_120['Lon_2'][:]]
# y_values19_120min = [csv19_20_120['Ini_Lat'][:], csv19_20_120['Lat_2'][:]]
# x_values20_120min = [csv20_21_120['Ini_Lon'][:], csv20_21_120['Lon_2'][:]]
# y_values20_120min = [csv20_21_120['Ini_Lat'][:], csv20_21_120['Lat_2'][:]]
# x_values21_120min = [csv21_22_120['Ini_Lon'][:], csv21_22_120['Lon_2'][:]]
# y_values21_120min = [csv21_22_120['Ini_Lat'][:], csv21_22_120['Lat_2'][:]]
# x_values22_120min = [csv22_23_120['Ini_Lon'][:], csv22_23_120['Lon_2'][:]]
# y_values22_120min = [csv22_23_120['Ini_Lat'][:], csv22_23_120['Lat_2'][:]]
# x_values23_120min = [csv23_0_120['Ini_Lon'][:], csv23_0_120['Lon_2'][:]]
# y_values23_120min = [csv23_0_120['Ini_Lat'][:], csv23_0_120['Lat_2'][:]]
# x_values00_120min = [csv00_01_120['Ini_Lon'][:], csv00_01_120['Lon_2'][:]]
# y_values00_120min = [csv00_01_120['Ini_Lat'][:], csv00_01_120['Lat_2'][:]]
# x_values01_120min = [csv01_02_120['Ini_Lon'][:], csv01_02_120['Lon_2'][:]]
# y_values01_120min = [csv01_02_120['Ini_Lat'][:], csv01_02_120['Lat_2'][:]]
# x_values02_120min = [csv02_03_120['Ini_Lon'][:], csv02_03_120['Lon_2'][:]]
# y_values02_120min = [csv02_03_120['Ini_Lat'][:], csv02_03_120['Lat_2'][:]]
# x_values03_120min = [csv03_04_120['Ini_Lon'][:], csv03_04_120['Lon_2'][:]]
# y_values03_120min = [csv03_04_120['Ini_Lat'][:], csv03_04_120['Lat_2'][:]]
# x_values04_120min = [csv04_05_120['Ini_Lon'][:], csv04_05_120['Lon_2'][:]]
# y_values04_120min = [csv04_05_120['Ini_Lat'][:], csv04_05_120['Lat_2'][:]]
# x_values05_120min = [csv05_06_120['Ini_Lon'][:], csv05_06_120['Lon_2'][:]]
# y_values05_120min = [csv05_06_120['Ini_Lat'][:], csv05_06_120['Lat_2'][:]]
# x_values06_120min = [csv06_07_120['Ini_Lon'][:], csv06_07_120['Lon_2'][:]]
# y_values06_120min = [csv06_07_120['Ini_Lat'][:], csv06_07_120['Lat_2'][:]]
# x_values07_120min = [csv07_08_120['Ini_Lon'][:], csv07_08_120['Lon_2'][:]]
# y_values07_120min = [csv07_08_120['Ini_Lat'][:], csv07_08_120['Lat_2'][:]]

x_values19_Severe = [csv19_20_Severe['Ini_Lon'][:], csv19_20_Severe['Lon_2'][:]]
y_values19_Severe = [csv19_20_Severe['Ini_Lat'][:], csv19_20_Severe['Lat_2'][:]]
x_values20_Severe = [csv20_21_Severe['Ini_Lon'][:], csv20_21_Severe['Lon_2'][:]]
y_values20_Severe = [csv20_21_Severe['Ini_Lat'][:], csv20_21_Severe['Lat_2'][:]]
x_values21_Severe = [csv21_22_Severe['Ini_Lon'][:], csv21_22_Severe['Lon_2'][:]]
y_values21_Severe = [csv21_22_Severe['Ini_Lat'][:], csv21_22_Severe['Lat_2'][:]]
x_values22_Severe = [csv22_23_Severe['Ini_Lon'][:], csv22_23_Severe['Lon_2'][:]]
y_values22_Severe = [csv22_23_Severe['Ini_Lat'][:], csv22_23_Severe['Lat_2'][:]]
x_values23_Severe = [csv23_0_Severe['Ini_Lon'][:], csv23_0_Severe['Lon_2'][:]]
y_values23_Severe = [csv23_0_Severe['Ini_Lat'][:], csv23_0_Severe['Lat_2'][:]]
x_values00_Severe = [csv00_01_Severe['Ini_Lon'][:], csv00_01_Severe['Lon_2'][:]]
y_values00_Severe = [csv00_01_Severe['Ini_Lat'][:], csv00_01_Severe['Lat_2'][:]]
x_values01_Severe = [csv01_02_Severe['Ini_Lon'][:], csv01_02_Severe['Lon_2'][:]]
y_values01_Severe = [csv01_02_Severe['Ini_Lat'][:], csv01_02_Severe['Lat_2'][:]]
x_values02_Severe = [csv02_03_Severe['Ini_Lon'][:], csv02_03_Severe['Lon_2'][:]]
y_values02_Severe = [csv02_03_Severe['Ini_Lat'][:], csv02_03_Severe['Lat_2'][:]]
x_values03_Severe = [csv03_04_Severe['Ini_Lon'][:], csv03_04_Severe['Lon_2'][:]]
y_values03_Severe = [csv03_04_Severe['Ini_Lat'][:], csv03_04_Severe['Lat_2'][:]]
# x_values04_Severe = [csv04_05_Severe['Ini_Lon'][:], csv04_05_Severe['Lon_2'][:]]
# y_values04_Severe = [csv04_05_Severe['Ini_Lat'][:], csv04_05_Severe['Lat_2'][:]]
# x_values05_Severe = [csv05_06_Severe['Ini_Lon'][:], csv05_06_Severe['Lon_2'][:]]
# y_values05_Severe = [csv05_06_Severe['Ini_Lat'][:], csv05_06_Severe['Lat_2'][:]]
# x_values06_Severe = [csv06_07_Severe['Ini_Lon'][:], csv06_07_Severe['Lon_2'][:]]
# y_values06_Severe = [csv06_07_Severe['Ini_Lat'][:], csv06_07_Severe['Lat_2'][:]]
# x_values07_Severe = [csv07_08_Severe['Ini_Lon'][:], csv07_08_Severe['Lon_2'][:]]
# y_values07_Severe = [csv07_08_Severe['Ini_Lat'][:], csv07_08_Severe['Lat_2'][:]]

x_values19_Supercell = [csv19_20_Supercell['Ini_Lon'][:], csv19_20_Supercell['Lon_2'][:]]
y_values19_Supercell = [csv19_20_Supercell['Ini_Lat'][:], csv19_20_Supercell['Lat_2'][:]]
x_values20_Supercell = [csv20_21_Supercell['Ini_Lon'][:], csv20_21_Supercell['Lon_2'][:]]
y_values20_Supercell = [csv20_21_Supercell['Ini_Lat'][:], csv20_21_Supercell['Lat_2'][:]]
x_values21_Supercell = [csv21_22_Supercell['Ini_Lon'][:], csv21_22_Supercell['Lon_2'][:]]
y_values21_Supercell = [csv21_22_Supercell['Ini_Lat'][:], csv21_22_Supercell['Lat_2'][:]]
x_values22_Supercell = [csv22_23_Supercell['Ini_Lon'][:], csv22_23_Supercell['Lon_2'][:]]
y_values22_Supercell = [csv22_23_Supercell['Ini_Lat'][:], csv22_23_Supercell['Lat_2'][:]]
x_values23_Supercell = [csv23_0_Supercell['Ini_Lon'][:], csv23_0_Supercell['Lon_2'][:]]
y_values23_Supercell = [csv23_0_Supercell['Ini_Lat'][:], csv23_0_Supercell['Lat_2'][:]]
x_values00_Supercell = [csv00_01_Supercell['Ini_Lon'][:], csv00_01_Supercell['Lon_2'][:]]
y_values00_Supercell = [csv00_01_Supercell['Ini_Lat'][:], csv00_01_Supercell['Lat_2'][:]]
x_values01_Supercell = [csv01_02_Supercell['Ini_Lon'][:], csv01_02_Supercell['Lon_2'][:]]
y_values01_Supercell = [csv01_02_Supercell['Ini_Lat'][:], csv01_02_Supercell['Lat_2'][:]]
x_values02_Supercell = [csv02_03_Supercell['Ini_Lon'][:], csv02_03_Supercell['Lon_2'][:]]
y_values02_Supercell = [csv02_03_Supercell['Ini_Lat'][:], csv02_03_Supercell['Lat_2'][:]]
x_values03_Supercell = [csv03_04_Supercell['Ini_Lon'][:], csv03_04_Supercell['Lon_2'][:]]
y_values03_Supercell = [csv03_04_Supercell['Ini_Lat'][:], csv03_04_Supercell['Lat_2'][:]]
# x_values04_Supercell = [csv04_05_Supercell['Ini_Lon'][:], csv04_05_Supercell['Lon_2'][:]]
# y_values04_Supercell = [csv04_05_Supercell['Ini_Lat'][:], csv04_05_Supercell['Lat_2'][:]]
# x_values05_Supercell = [csv05_06_Supercell['Ini_Lon'][:], csv05_06_Supercell['Lon_2'][:]]
# y_values05_Supercell = [csv05_06_Supercell['Ini_Lat'][:], csv05_06_Supercell['Lat_2'][:]]
# x_values06_Supercell = [csv06_07_Supercell['Ini_Lon'][:], csv06_07_Supercell['Lon_2'][:]]
# y_values06_Supercell = [csv06_07_Supercell['Ini_Lat'][:], csv06_07_Supercell['Lat_2'][:]]
# x_values07_Supercell = [csv07_08_Supercell['Ini_Lon'][:], csv07_08_Supercell['Lon_2'][:]]
# y_values07_Supercell = [csv07_08_Supercell['Ini_Lat'][:], csv07_08_Supercell['Lat_2'][:]]

x_values19_Tornado = [csv19_20_Tornado['Ini_Lon'][:], csv19_20_Tornado['Lon_2'][:]]
y_values19_Tornado = [csv19_20_Tornado['Ini_Lat'][:], csv19_20_Tornado['Lat_2'][:]]
x_values20_Tornado = [csv20_21_Tornado['Ini_Lon'][:], csv20_21_Tornado['Lon_2'][:]]
y_values20_Tornado = [csv20_21_Tornado['Ini_Lat'][:], csv20_21_Tornado['Lat_2'][:]]
x_values21_Tornado = [csv21_22_Tornado['Ini_Lon'][:], csv21_22_Tornado['Lon_2'][:]]
y_values21_Tornado = [csv21_22_Tornado['Ini_Lat'][:], csv21_22_Tornado['Lat_2'][:]]
x_values22_Tornado = [csv22_23_Tornado['Ini_Lon'][:], csv22_23_Tornado['Lon_2'][:]]
y_values22_Tornado = [csv22_23_Tornado['Ini_Lat'][:], csv22_23_Tornado['Lat_2'][:]]
x_values23_Tornado = [csv23_0_Tornado['Ini_Lon'][:], csv23_0_Tornado['Lon_2'][:]]
y_values23_Tornado = [csv23_0_Tornado['Ini_Lat'][:], csv23_0_Tornado['Lat_2'][:]]
x_values00_Tornado = [csv00_01_Tornado['Ini_Lon'][:], csv00_01_Tornado['Lon_2'][:]]
y_values00_Tornado = [csv00_01_Tornado['Ini_Lat'][:], csv00_01_Tornado['Lat_2'][:]]
x_values01_Tornado = [csv01_02_Tornado['Ini_Lon'][:], csv01_02_Tornado['Lon_2'][:]]
y_values01_Tornado = [csv01_02_Tornado['Ini_Lat'][:], csv01_02_Tornado['Lat_2'][:]]
x_values02_Tornado = [csv02_03_Tornado['Ini_Lon'][:], csv02_03_Tornado['Lon_2'][:]]
y_values02_Tornado = [csv02_03_Tornado['Ini_Lat'][:], csv02_03_Tornado['Lat_2'][:]]
x_values03_Tornado = [csv03_04_Tornado['Ini_Lon'][:], csv03_04_Tornado['Lon_2'][:]]
y_values03_Tornado = [csv03_04_Tornado['Ini_Lat'][:], csv03_04_Tornado['Lat_2'][:]]
# x_values04_Tornado = [csv04_05_Tornado['Ini_Lon'][:], csv04_05_Tornado['Lon_2'][:]]
# y_values04_Tornado = [csv04_05_Tornado['Ini_Lat'][:], csv04_05_Tornado['Lat_2'][:]]
# x_values05_Tornado = [csv05_06_Tornado['Ini_Lon'][:], csv05_06_Tornado['Lon_2'][:]]
# y_values05_Tornado = [csv05_06_Tornado['Ini_Lat'][:], csv05_06_Tornado['Lat_2'][:]]
# x_values06_Tornado = [csv06_07_Tornado['Ini_Lon'][:], csv06_07_Tornado['Lon_2'][:]]
# y_values06_Tornado = [csv06_07_Tornado['Ini_Lat'][:], csv06_07_Tornado['Lat_2'][:]]
# x_values07_Tornado = [csv07_08_Tornado['Ini_Lon'][:], csv07_08_Tornado['Lon_2'][:]]
# y_values07_Tornado = [csv07_08_Tornado['Ini_Lat'][:], csv07_08_Tornado['Lat_2'][:]]

linestyle = "-"
linestyle2 = "-"
linestyle3 = "-"
linestyle4 = "-"
width1 = 5.0
width2 = 10.0
width3 = 14.0

ax.plot(x_values18, y_values18, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values19, y_values19, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values20, y_values20, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values21, y_values21, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values22, y_values22, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values23, y_values23, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values00, y_values00, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values01, y_values01, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values02, y_values02, linestyle=linestyle, color='#999999', linewidth=width1)
ax.plot(x_values03, y_values03, linestyle=linestyle, color='#999999', linewidth=width1)
#ax.plot(x_values04, y_values04, linestyle=linestyle, color='black', linewidth=width1)
#ax.plot(x_values05, y_values05, linestyle=linestyle, color='black', linewidth=width1, alpha=0.4)
#ax.plot(x_values06, y_values06, linestyle=linestyle, color='black', linewidth=width1, alpha=0.4)
#ax.plot(x_values07, y_values07, linestyle=linestyle, color='black', linewidth=width1, alpha=0.4)

#ax.plot(x_values19_Supercell, y_values19_Supercell, linestyle=linestyle, color='green', linewidth=width2)
ax.plot(x_values20_Supercell, y_values20_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values21_Supercell, y_values21_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values22_Supercell, y_values22_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values23_Supercell, y_values23_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values00_Supercell, y_values00_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values01_Supercell, y_values01_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values02_Supercell, y_values02_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
ax.plot(x_values03_Supercell, y_values03_Supercell, linestyle=linestyle2, color='#E69F00', linewidth=width2)
#ax.plot(x_values04_Supercell, y_values04_Supercell, linestyle=linestyle, color='lime', linewidth=width2)
#ax.plot(x_values05_Supercell, y_values05_Supercell, linestyle=linestyle, color='green', linewidth=width2, alpha=0.4)
#ax.plot(x_values06_Supercell, y_values06_Supercell, linestyle=linestyle, color='green', linewidth=width2, alpha=0.4)
#ax.plot(x_values07_Supercell, y_values07_Supercell, linestyle=linestyle, color='green', linewidth=width2, alpha=0.4)

#ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle, color='blue', linewidth=width2)
#ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle, color='blue', linewidth=width2)
ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle3, color='#0072B2', linewidth=width2)
#ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle, color='blue', linewidth=width2)
#ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle, color='blue', linewidth=width2, alpha=0.4)
#ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle, color='blue', linewidth=width2, alpha=0.4)
#ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle, color='blue', linewidth=width2, alpha=0.4)

#ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3)
#ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3)
ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle4, color='#CC79A7', linewidth=width3)
#ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3)
#ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3, alpha=0.4)
#ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3, alpha=0.4)
#ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle, color='goldenrod', linewidth=width3, alpha=0.4)


ax.plot(1,1,linestyle="-", color='black', linewidth=10, label='Non-Supercell')
ax.plot(1,1,linestyle="-", color='lime', linewidth=10, label =  "Supercell")
ax.plot(1,1,linestyle="-", color="blue", linewidth=10, label =  "Severe")
ax.plot(1,1,linestyle="-", color='goldenrod', linewidth=10, label =  "Tornadic")

dfType = pd.read_csv('D:/THESIS/__UNL MS Thesis (MAIN)__/1 - Cell Tracking/Cell Tracking Map/QC_Cell_Tracks_Master_PostBuffer.csv')
OPW1lats = np.asarray(dfType[dfType.Grouping2=='OPW1']['Ini_Lat'])
OPW2lats = np.asarray(dfType[dfType.Grouping2=='OPW2']['Ini_Lat'])
OPW3lats = np.asarray(dfType[dfType.Grouping2=='OPW3']['Ini_Lat'])
OPW4lats = np.asarray(dfType[dfType.Grouping2=='OPW4']['Ini_Lat'])
OPW1lons = np.asarray(dfType[dfType.Grouping2=='OPW1']['Ini_Lon'])
OPW2lons = np.asarray(dfType[dfType.Grouping2=='OPW2']['Ini_Lon'])
OPW3lons = np.asarray(dfType[dfType.Grouping2=='OPW3']['Ini_Lon'])
OPW4lons = np.asarray(dfType[dfType.Grouping2=='OPW4']['Ini_Lon'])

OPE1lats = np.asarray(dfType[dfType.Grouping2=='OPE1']['Ini_Lat'])
OPE2lats = np.asarray(dfType[dfType.Grouping2=='OPE2']['Ini_Lat'])
OPE3lats = np.asarray(dfType[dfType.Grouping2=='OPE3']['Ini_Lat'])
OPE1lons = np.asarray(dfType[dfType.Grouping2=='OPE1']['Ini_Lon'])
OPE2lons = np.asarray(dfType[dfType.Grouping2=='OPE2']['Ini_Lon'])
OPE3lons = np.asarray(dfType[dfType.Grouping2=='OPE3']['Ini_Lon'])

BDW1lats = np.asarray(dfType[dfType.Grouping2=='BDW1']['Ini_Lat'])
BDW2lats = np.asarray(dfType[dfType.Grouping2=='BDW2']['Ini_Lat'])
BDW3lats = np.asarray(dfType[dfType.Grouping2=='BDW3']['Ini_Lat'])
BDW4lats = np.asarray(dfType[dfType.Grouping2=='BDW4']['Ini_Lat'])
BDW1lons = np.asarray(dfType[dfType.Grouping2=='BDW1']['Ini_Lon'])
BDW2lons = np.asarray(dfType[dfType.Grouping2=='BDW2']['Ini_Lon'])
BDW3lons = np.asarray(dfType[dfType.Grouping2=='BDW3']['Ini_Lon'])
BDW4lons = np.asarray(dfType[dfType.Grouping2=='BDW4']['Ini_Lon'])

BDE1lats = np.asarray(dfType[dfType.Grouping2=='BDE1']['Ini_Lat'])
BDE2lats = np.asarray(dfType[dfType.Grouping2=='BDE2']['Ini_Lat'])
BDE3lats = np.asarray(dfType[dfType.Grouping2=='BDE3']['Ini_Lat'])
BDE1lons = np.asarray(dfType[dfType.Grouping2=='BDE1']['Ini_Lon'])
BDE2lons = np.asarray(dfType[dfType.Grouping2=='BDE2']['Ini_Lon'])
BDE3lons = np.asarray(dfType[dfType.Grouping2=='BDE3']['Ini_Lon'])

rad1 = 0.06
rad2 = 0.05
rad3 = 0.04
labfont = 30

# Define the extent limits
lon_min, lon_max = -100.25, -94.0
lat_min, lat_max = 32.85, 37.30

# Define the clipping rectangle with correct bounds
clip_rect = Rectangle(
    (lon_min, lat_min),  # Lower-left corner (Longitude min, Latitude min)
    lon_max - lon_min,   # Width (Longitude range)
    lat_max - lat_min,   # Height (Latitude range)
    transform=ax.transData, clip_on=True,
    facecolor='none', 
    edgecolor='none'
)
ax.add_patch(clip_rect)


for i in range(len(OPW1lats)):
    circle_outline = patches.Circle((OPW1lons[i], OPW1lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPW1lons[i], OPW1lats[i]), radius=rad2, color='cyan', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPW1lons[i], OPW1lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPW1lons[i], OPW1lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPW1']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)

for i in range(len(OPW2lats)):
    circle_outline = patches.Circle((OPW2lons[i], OPW2lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPW2lons[i], OPW2lats[i]), radius=rad2, color='cyan', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPW2lons[i], OPW2lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPW2lons[i], OPW2lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPW2']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)

for i in range(len(OPW3lats)):
    #if OPW3lats[i] > 33.2:
        circle_outline = patches.Circle((OPW3lons[i], OPW3lats[i]), radius=rad1, color='black', zorder=2)
        circle_outline.set_clip_path(clip_rect)
        ax.add_patch(circle_outline)
        circle1 = patches.Circle((OPW3lons[i], OPW3lats[i]), radius=rad2, color='cyan', zorder=3)
        circle1.set_clip_path(clip_rect)
        ax.add_patch(circle1)
        #circle2 = patches.Circle((OPW3lons[i], OPW3lats[i]), radius=rad3, color='black', zorder=4)
        #ax.add_patch(circle2)
        text = ax.text(OPW3lons[i], OPW3lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPW3']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)
        text.set_clip_path(clip_rect)       
        
for i in range(len(OPW4lats)):
    circle_outline = patches.Circle((OPW4lons[i], OPW4lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPW4lons[i], OPW4lats[i]), radius=rad2, color='cyan', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPW4lons[i], OPW4lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPW4lons[i], OPW4lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPW4']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)
    
for i in range(len(OPE1lats)):
    circle_outline = patches.Circle((OPE1lons[i], OPE1lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPE1lons[i], OPE1lats[i]), radius=rad2, color='#E69F00', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPE1lons[i], OPE1lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPE1lons[i], OPE1lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPE1']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)

for i in range(len(OPE2lats)):
    circle_outline = patches.Circle((OPE2lons[i], OPE2lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPE2lons[i], OPE2lats[i]), radius=rad2, color='#E69F00', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPE2lons[i], OPE2lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPE2lons[i], OPE2lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPE2']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)

for i in range(len(OPE3lats)):
    circle_outline = patches.Circle((OPE3lons[i], OPE3lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((OPE3lons[i], OPE3lats[i]), radius=rad2, color='#E69F00', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((OPE3lons[i], OPE3lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(OPE3lons[i], OPE3lats[i], str(np.asarray(dfType[dfType.Grouping2=='OPE3']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)
    
for i in range(len(BDW1lats)):
    circle_outline = patches.Circle((BDW1lons[i], BDW1lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((BDW1lons[i], BDW1lats[i]), radius=rad2, color='#009E73', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((BDW1lons[i], BDW1lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(BDW1lons[i], BDW1lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDW1']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)
    
for i in range(len(BDW2lats)):
    circle_outline = patches.Circle((BDW2lons[i], BDW2lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((BDW2lons[i], BDW2lats[i]), radius=rad2, color='#009E73', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((BDW2lons[i], BDW2lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(BDW2lons[i], BDW2lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDW2']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)

for i in range(len(BDW3lats)):
    circle_outline = patches.Circle((BDW3lons[i], BDW3lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((BDW3lons[i], BDW3lats[i]), radius=rad2, color='#009E73', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((BDW3lons[i], BDW3lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(BDW3lons[i], BDW3lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDW3']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)
    
for i in range(len(BDW4lats)):
    circle_outline = patches.Circle((BDW4lons[i], BDW4lats[i]), radius=rad1, color='black', zorder=2)
    ax.add_patch(circle_outline)
    circle1 = patches.Circle((BDW4lons[i], BDW4lats[i]), radius=rad2, color='#009E73', zorder=3)
    ax.add_patch(circle1)
    #circle2 = patches.Circle((BDW4lons[i], BDW4lats[i]), radius=rad3, color='black', zorder=4)
    #ax.add_patch(circle2)
    ax.text(BDW4lons[i], BDW4lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDW4']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5)    
    
for i in range(len(BDE1lats)):
    if BDE1lats[i] < 37.35:
        circle_outline = patches.Circle((BDE1lons[i], BDE1lats[i]), radius=rad1, color='black', zorder=2, clip_on=True)
        circle_outline.set_clip_path(clip_rect)
        ax.add_patch(circle_outline)
        circle1 = patches.Circle((BDE1lons[i], BDE1lats[i]), radius=rad2, color='#009E73', zorder=3, clip_on=True)
        circle1.set_clip_path(clip_rect)
        ax.add_patch(circle1)
        #circle2 = patches.Circle((BDE1lons[i], BDE1lats[i]), radius=rad3, color='black', zorder=4)
        #ax.add_patch(circle2)
        text = ax.text(BDE1lons[i], BDE1lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDE1']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5, clip_on=True)
        text.set_clip_path(clip_rect)

for i in range(len(BDE2lats)):
    if BDE2lats[i] < 37.35:
        circle_outline = patches.Circle((BDE2lons[i], BDE2lats[i]), radius=rad1, color='black', zorder=2, clip_on=True)
        circle_outline.set_clip_path(clip_rect)
        ax.add_patch(circle_outline)
        circle1 = patches.Circle((BDE2lons[i], BDE2lats[i]), radius=rad2, color='#009E73', zorder=3, clip_on=True)
        circle1.set_clip_path(clip_rect)
        ax.add_patch(circle1)
        #circle2 = patches.Circle((BDE2lons[i], BDE2lats[i]), radius=rad3, color='black', zorder=4)
        #ax.add_patch(circle2)
        text = ax.text(BDE2lons[i], BDE2lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDE2']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5, clip_on=True)
        text.set_clip_path(clip_rect)

for i in range(len(BDE3lats)):
    if BDE3lats[i] < 37.35:
        circle_outline = patches.Circle((BDE3lons[i], BDE3lats[i]), radius=rad1, color='black', zorder=2, clip_on=True)
        circle_outline.set_clip_path(clip_rect)
        ax.add_patch(circle_outline)
        circle1 = patches.Circle((BDE3lons[i], BDE3lats[i]), radius=rad2, color='#009E73', zorder=3, clip_on=True)
        circle1.set_clip_path(clip_rect)
        ax.add_patch(circle1)
        #circle2 = patches.Circle((BDE3lons[i], BDE3lats[i]), radius=rad3, color='black', zorder=4)
        #ax.add_patch(circle2)
        text = ax.text(BDE3lons[i], BDE3lats[i], str(np.asarray(dfType[dfType.Grouping2=='BDE3']['GroupingLabel'])[0]), fontsize=labfont, color='black', ha='center', va='center', weight='bold', zorder=5, clip_on=True)
        text.set_clip_path(clip_rect)

title = "22 May 2019\nObserved Storm Tracks (18 - 4Z)"
ax.set_title(title, fontsize=45, fontweight='bold')

#plt.legend(loc='lower right', fontsize = 55,shadow=True, title="Storm Type")
fig.set_facecolor('whitesmoke')

# Define legend elements
legend_elements = [
    # Subregions Section
    mpatches.Patch(color='white', label=r'$\bf{Subregions}$'),
    plt.Line2D([0], [0], marker='o', linestyle='', markerfacecolor='cyan', markeredgecolor='black', markeredgewidth=4, markersize=36, label='Warm Sector - W'),
    plt.Line2D([0], [0], marker='o', linestyle='', markerfacecolor='#E69F00', markeredgecolor='black', markeredgewidth=4, markersize=36, label='Warm Sector - E'),
    plt.Line2D([0], [0], marker='o', linestyle='', markerfacecolor='#009E73', markeredgecolor='black', markeredgewidth=4, markersize=36, label='Boundary'),
    
    # Spacer
    mpatches.Patch(color='white', label=" "),

    # Storm Type Section
    mpatches.Patch(color='white', label=r'$\bf{Storm\ Type}$'),
#     plt.Line2D([0], [0], linestyle="-", color='black', linewidth=10, label='Non-Supercell'),
#     plt.Line2D([0], [0], linestyle="-", color='goldenrod', linewidth=10, label='Supercell'),
#     plt.Line2D([0], [0], linestyle="-", color="teal", linewidth=10, label='Severe'),
#     plt.Line2D([0], [0], linestyle="-", color='violet', linewidth=10, label='Tornadic'),
    plt.Line2D([0], [0], linestyle="-", color='#999999', linewidth=10, label='Non-Supercell'),
    plt.Line2D([0], [0], linestyle="-", color='#E69F00', linewidth=10, label='Supercell'),
    plt.Line2D([0], [0], linestyle="-", color="#0072B2", linewidth=10, label='Severe'),
    plt.Line2D([0], [0], linestyle="-", color='#CC79A7', linewidth=10, label='Tornadic'),
]

# Create the legend with proper formatting
legend = ax.legend(handles=legend_elements, loc='lower right', fontsize=48, title_fontsize=48, frameon=True, shadow=True, title="",
                   handletextpad=1, borderpad=0.5, labelspacing=0.5, framealpha=1, edgecolor="black")

# Adjust legend background color
legend.get_frame().set_facecolor('white')

plt.show()

In [66]:
OPE3lats

array([35.36598, 35.40231, 35.65755, 35.63036, 35.85293, 36.70969,
       35.96503, 36.36926])

In [29]:
OPWlats = np.asarray(dfType[dfType.Grouping=='OPW']['Ini_Lat'])
OPWlons = np.asarray(dfType[dfType.Grouping=='OPW']['Ini_Lon'])

OPElats = np.asarray(dfType[dfType.Grouping=='OPE']['Ini_Lat'])
OPElons = np.asarray(dfType[dfType.Grouping=='OPE']['Ini_Lon'])

BDWlats = np.asarray(dfType[dfType.Grouping=='BDW']['Ini_Lat'])
BDWlons = np.asarray(dfType[dfType.Grouping=='BDW']['Ini_Lon'])

BDElats = np.asarray(dfType[dfType.Grouping=='BDE']['Ini_Lat'])
BDElons = np.asarray(dfType[dfType.Grouping=='BDE']['Ini_Lon'])

type(OPWlats)
#for i in OPWlats:
#    print(OPWlats[i])#, OPWlons[i])
#print(dfType[dfType.Grouping=='OPW']['Ini_Lat']
#for i in range(len(dfType[dfType.Grouping=='OPW'])):
#    print(dfType[dfType.Grouping=='OPW']['Ini_Lon'][i])


numpy.ndarray

In [35]:
for i in range(len(OPWlats)):
    print(OPWlats[i], OPWlons[i])

33.97577 -98.9567
34.42155 -98.65039
33.73985 -99.18623
33.37762 -99.27945
34.46386 -97.63286
34.50377 -97.43682
32.90389 -99.70187
33.57045 -99.32433
34.30355 -98.60541
34.46688 -97.80047
34.56154 -97.84374
34.9207 -98.52563
33.77514 -99.20477
34.18407 -98.84023
34.60451 -98.59406
34.67411 -98.44359
34.18887 -99.18777
34.38779 -99.88203
34.22089 -99.64944
34.74295 -99.39772
34.99516 -99.28853
35.17844 -99.09502
34.99018 -98.2382
33.8219 -99.29974
34.06586 -98.83989
34.1944 -98.71913
34.44884 -98.56797
34.27695 -98.73127
35.08721 -98.47652
34.87672 -98.45626
33.98403 -99.01173
34.10883 -98.98952
34.34731 -98.6496
34.66486 -98.78335
33.4754 -99.24889
33.69658 -99.08875
34.661 -97.36888


In [3]:
year=2019
month=5
day = 23
hour = 2

time_start = datetime(int(year), int(month), int(day), int(hour), 0) # Our specified time
hour = time_start.hour
if hour < 10:
    hour = '0'+str(hour)
day = time_start.day
if day < 10:
    day = '0'+str(day)
month = time_start.month
if month < 10:
    month = '0'+str(month)

#======
file = 0

## 1    
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need1!")
    except:
        file = 0
        print("No file yet...")

## 2
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need2!")
    except:
        file = 0
        print("No file yet...")
        
## 3
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need3!")
    except:
        file = 0
        print("No file yet...")

## 4
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need4!")
    except:
        file = 0
        print("No file yet...")        
        
## 1b
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need1b!")
    except:
        file = 0
        print("No file yet...")

## 2b
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need2b!")
    except:
        file = 0
        print("No file yet...")
        
## 3b
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need3b!")
    except:
        file = 0
        print("No file yet...")

## 4b
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need4b!")
    except:
        file = 0
        print("No file yet...")


## 5
#if file == 0:
#    try:
#        cat = TDSCatalog('https://www.ncdc.noaa.gov/thredds/catalog/model-rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
#        file = 1
#        print("We have the file we need!")
#    except:
#        file = 0
#        print("No file yet...")
        
## 6
#if file == 0:
#    try:
#        cat = TDSCatalog('https://www.ncdc.noaa.gov/thredds/catalog/model-rap130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
#        file = 1
#        print("We have the file we need...rap130anal!")
#    except:
#        file = 0
#        print("No file yet...rap130anal")

## 7
#if file == 0:
#    try:
#        cat = TDSCatalog('https://www.ncdc.noaa.gov/thredds/catalog/model-rap252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
#        file = 1
#        print("We have the file we need...rap252anal!")
#    except:
#        file = 0
#        print("No file yet...rap252anal")

## 8
#if file == 0:
#    try:
#        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
#        file = 1
#        print("We have the file we need!")
#    except:
#        file = 0
#        print("No file yet...")


## 9
if file == 0:
    try:
        cat = TDSCatalog('http://nomads.ncdc.noaa.gov/thredds/catalog/rap130/'+str(time_start.year)+'0'+str(time_start.month)+'/'+str(time_start.year)+'0'+str(time_start.month)+str(time_start.day)+'/catalog.html?dataset=rap130/'+str(time_start.year)+'0'+str(time_start.month)+'/'+str(time_start.year)+'0'+str(time_start.month)+str(time_start.day)+'/rap_130_'+str(time_start.year)+'0'+str(time_start.month)+str(time_start.day)+'_'+str(time_start.hour)+'00_001.grb2')
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("No file yet...")

## 10
if file == 0:
    try:
        cat = TDSCatalog('http://nomads.ncdc.noaa.gov/thredds/catalog/rap130/'+str(year)+str(month)+'/'+str(year)+str(month)+str(day)+'/catalog.html?dataset=rap130/'+str(year)+str(month)+'/'+str(year)+str(month)+str(day)+'/rap_130_'+str(year)+str(month)+str(day)+'_'+str(UTC)+'_000.grb2')
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("No file yet...")

## 11
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/rap130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("No file yet...")

## 12
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncdc.noaa.gov/thredds/catalog/model-rap252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("No file yet...")

## 13
#if file == 0:
#    try:
#        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-rap252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap252anl-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2') 
#        file = 1
#        print("We have the file we need!")
#    except:
#        file = 0
#        print("No file yet...")

## 14
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc130anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc2anl_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2') 
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("No file yet...")

## 15
if file == 0:
    try:
        cat = TDSCatalog('https://www.ncei.noaa.gov/thredds/catalog/model-ruc252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=ruc252anl/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/ruc2anl_252_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_000.grb2')
        file = 1
        print("We have the file we need!")
    except:
        file = 0
        print("We didn't get any file!")
#=====
    
#cat = TDSCatalog('https://www.ncdc.noaa.gov/thredds/catalog/model-rap130-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/catalog.html?dataset=rap130-old/'+str(time_start.year)+str(month)+'/'+str(time_start.year)+str(month)+str(day)+'/rap_130_'+str(time_start.year)+str(month)+str(day)+'_'+str(hour)+'00_020.grb2')

latest_ds = list(cat.datasets.values())[0]
ncss = NCSS(latest_ds.access_urls['NetcdfSubset'])
query = ncss.query()
query.variables('Vertical_velocity_pressure_isobaric').variables('Convective_available_potential_energy_surface').variables('u-component_of_wind_isobaric').variables('v-component_of_wind_isobaric').variables('Storm_relative_helicity_height_above_ground_layer').variables('Pressure_surface').variables('Dewpoint_temperature_height_above_ground').variables('Temperature_height_above_ground').variables('Vertical_u-component_shear_height_above_ground_layer').variables('Vertical_v-component_shear_height_above_ground_layer').variables('Geopotential_height_isobaric').variables('Geopotential_height_surface').variables('u-component_of_wind_height_above_ground').variables('v-component_of_wind_height_above_ground').variables('Relative_humidity_isobaric').variables('Temperature_isobaric')
data1 = ncss.get_data(query)

dtime = data1.variables['Geopotential_height_isobaric'].dimensions[0]
dlev = data1.variables['Geopotential_height_isobaric'].dimensions[1]
dlat = data1.variables['Geopotential_height_isobaric'].dimensions[2] #y
dlon = data1.variables['Geopotential_height_isobaric'].dimensions[3] #x

SFCP = (np.asarray(data1.variables['Pressure_surface'][:])/100.) * units('hPa')
Td = (np.asarray(data1.variables['Dewpoint_temperature_height_above_ground'][:]) * units('kelvin')).to('degC')
T = np.asarray(data1.variables['Temperature_height_above_ground'][:]) * units('kelvin')
hgt = np.asarray(data1.variables['Geopotential_height_isobaric'][:]) * units('meter')
sfc_hgt = np.asarray(data1.variables['Geopotential_height_surface'][:]) * units('meter')
uwnd = np.asarray(data1.variables['u-component_of_wind_isobaric'][:]) * units('m/s')
vwnd = np.asarray(data1.variables['v-component_of_wind_isobaric'][:]) * units('m/s')
usfc = np.asarray(data1.variables['u-component_of_wind_height_above_ground'][:]) * units('m/s')
vsfc = np.asarray(data1.variables['v-component_of_wind_height_above_ground'][:]) * units('m/s')


lats_r = data1.variables[dlat][:]
lons_r= data1.variables[dlon][:]
lev = (np.asarray(data1.variables[dlev][:])/100.) * units('hPa')

# Set up our array of latitude and longitude values and transform to the desired projection.
crs = ccrs.PlateCarree()
#crlons, crlats = np.meshgrid(lons_r[:]*1000, lats_r[:]*1000)
crlons, crlats = np.meshgrid(lons_r[:]*1000, lats_r[:]*1000)
#trlatlons = crs.transform_points(ccrs.LambertConformal(central_longitude=-95, central_latitude=25, standard_parallels=None),crlons,crlats)
trlatlons = crs.transform_points(ccrs.LambertConformal(central_longitude=-95, central_latitude=25),crlons,crlats)

#trlatlons = crs.transform_points(ccrs.LambertConformal(central_longitude=-95, central_latitude=(flat-8), standard_parallels=None),crlons,crlats)

#trlatlons = crs.transform_points(ccrs.LambertConformal(central_longitude=265, central_latitude=25, standard_parallels=(25.,25.)),crlons,crlats)
trlons = trlatlons[:,:,0]
trlats = trlatlons[:,:,1]


D:\Anaconda3\envs\BL\lib\site-packages\siphon\catalog.py:292: UserWarning: URL https://www.ncei.noaa.gov/thredds/catalog/model-rap130anl-old/201905/20190523/catalog.html?dataset=rap130anl-old/201905/20190523/rap_130_20190523_0200_000.grb2 returned HTML. Changing to: https://www.ncei.noaa.gov/thredds/catalog/model-rap130anl-old/201905/20190523/catalog.xml?dataset=rap130anl-old/201905/20190523/rap_130_20190523_0200_000.grb2
  warnings.warn('URL {} returned HTML. Changing to: {}'.format(self.catalog_url,


We have the file we need1!


In [ ]:
import glob
import matplotlib.colors as colors

reader = shpreader.Reader(r"C:\Users\kyled\Desktop\Thesis GIS Data\County1010\countyl010g.shp")
counties = list(reader.geometries())
COUNTIES = cfeature.ShapelyFeature(counties, ccrs.PlateCarree())
proj = ccrs.PlateCarree()
df1 = pd.read_csv(r"C:\Users\kyled\Desktop\Round2.csv")

hours = ["18", "19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["18", "19", "20"]
#hours = ["21", "22", "23"]
#hours = ["00", "01", "02"]
#hours = ["04", "05", "06", "07"]
#hours = ["06", "07"]

for i in hours:
    #folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(i)
    folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\Round_2\_"+str(i)
    files = glob.glob(folder+'\*.csv')

    for j in range(0, len(files)):
    #for j in range(0, 11):
        df = pd.read_csv(files[j],header = None)
        df.fillna(0,inplace=True)
        data = df.to_numpy()
        #print(data)
        #print(files[j][41:], data.shape, np.amin(data), np.amax(data))
        if i == "18":
            day0 = "22"
        elif i == "19":
            day0 = "22"
        elif i == "20":
            day0 = "22"
        elif i == "21":
            day0 = "22"
        elif i == "22":
            day0 = "22"
        elif i == "23":
            day0 = "22"
        else:
            day0 = "23"
        
        title = str(day0)+" May 2019, "+str(i)+"z \n Observed Storm Tracks (by storm type) \n" + df1['param'][j]
        fig=plt.figure(figsize = (36,36))
        ax = plt.axes(projection=ccrs.PlateCarree())
        ax.set_title(title, fontsize=45, fontweight='bold')
        #ax.set_xlabel("test",size = 26)
        #ax.set_ylabel("test",size = 26,alpha=1.0)
        #ax.set_xlabel('lon')
        #ax.set_ylabel('lat')
        ax.set_xticks([-180,-120,-60,0,60,120,180])
        ax.set_yticks([-90,-60,-30,0,30,60,90])

        #ax.imshow(SFCP[0])
        ax.add_feature(cfeature.STATES.with_scale('50m'), linestyle='-', edgecolor='black', linewidth=1.5)
        ax.add_feature(COUNTIES, facecolor='none', edgecolor='black', linewidth=0.75)
        ax.set_extent([-100.73, -91.36, 32.52, 39.10])

        line = 3.0
        superline = 10.0
        c1 = 'orange'
        c2 = 'royalblue'
        c3 = 'green'
        linestyle1 = '-'
        linestyle2 = '--'
                
        #ax.plot(1,1,linestyle="--", color=c1, linewidth=5, label='Cell Tracks')
        #ax.plot(1,1,linestyle="--", color=c2, linewidth=5, label =  "Severe")
        #ax.plot(1,1,linestyle="--", color=c3, linewidth=5, label =  "Tornadic")
        ax.plot(1,1,linestyle="-", color='black', linewidth=10, label =  "Current Hour")

        #vmax = df1['highBound'][j]
        #vmin = df1['lowBound'][j]
        levels = range(int(df1['lowBound'][j]), int(df1['highBound'][j]), int(df1['cf_levels'][j]))
        #levels = np.array([int(df1['lowBound'][j]), int(df1['highBound'][j]), int(df1['cf_levels'][j])])
        #print(levels)

        def truncate_colormap(cmap, minval=0.0, maxval=1.0, n=20):
            new_cmap = colors.LinearSegmentedColormap.from_list(
                'trunc({n},{a:.2f},{b:.2f})'.format(n=cmap.name, a=minval, b=maxval),
                cmap(np.linspace(minval, maxval, n)))
            return new_cmap

        cmap_1 = plt.get_cmap('binary')
        cmap_2 = plt.get_cmap('Greys')
        cmap1 = truncate_colormap(cmap_1, 0, 0.5)
        cmap2 = truncate_colormap(cmap_2, 0.5, 1.0)

        cf = ax.contour(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap2) # Make a filled contour plot
        cf1 = ax.contourf(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap1) # Make a filled contour plot

        cbar = plt.colorbar(cf1, shrink=0.55, pad=0.01)
        cbar.ax.tick_params(labelsize=20)

        fig.set_facecolor('whitesmoke')
        plt.legend(loc='upper left', fontsize = 35,shadow=True)
        #fig.tight_layout()
        plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(df1['param'][j])+"_"+str(i)+"_"+str(j)+".png", bbox_inches='tight')
        #plt.show()
        plt.close(fig)
        plt.clf()
        
        print(df1['param'][j], i, j)
        j+=1
    #notify.send('figs for hour'+str(i)+' completed')

In [6]:
import glob
import matplotlib.colors as colors

reader = shpreader.Reader(r"C:\Users\kyled\Desktop\Thesis GIS Data\County1010\countyl010g.shp")
counties = list(reader.geometries())
COUNTIES = cfeature.ShapelyFeature(counties, ccrs.PlateCarree())
proj = ccrs.PlateCarree()
df1 = pd.read_csv(r"C:\Users\kyled\Desktop\Round2.csv")

hours = ["18", "19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["18", "19", "20"]
#hours = ["21", "22", "23"]
#hours = ["00", "01", "02"]
#hours = ["04", "05", "06", "07"]
#hours = ["06", "07"]

for i in hours:
    #folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(i)
    folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\Round_2\_"+str(i)
    files = glob.glob(folder+'\*.csv')

    for j in range(0, len(files)):
    #for j in range(0, 11):
        df = pd.read_csv(files[j],header = None)
        df.fillna(0,inplace=True)
        data = df.to_numpy()
        #print(data)
        #print(files[j][41:], data.shape, np.amin(data), np.amax(data))
        if i == "18":
            day0 = "22"
        elif i == "19":
            day0 = "22"
        elif i == "20":
            day0 = "22"
        elif i == "21":
            day0 = "22"
        elif i == "22":
            day0 = "22"
        elif i == "23":
            day0 = "22"
        else:
            day0 = "23"
        
        title = str(day0)+" May 2019, "+str(i)+"z \n Observed Storm Tracks (by storm type) \n" + df1['param'][j]
        fig=plt.figure(figsize = (36,36))
        ax = plt.axes(projection=ccrs.PlateCarree())
        ax.set_title(title, fontsize=45, fontweight='bold')
        #ax.set_xlabel("test",size = 26)
        #ax.set_ylabel("test",size = 26,alpha=1.0)
        #ax.set_xlabel('lon')
        #ax.set_ylabel('lat')
        ax.set_xticks([-180,-120,-60,0,60,120,180])
        ax.set_yticks([-90,-60,-30,0,30,60,90])

        #ax.imshow(SFCP[0])
        ax.add_feature(cfeature.STATES.with_scale('50m'), linestyle='-', edgecolor='black', linewidth=1.5)
        ax.add_feature(COUNTIES, facecolor='none', edgecolor='black', linewidth=0.75)
        ax.set_extent([-100.73, -91.36, 32.52, 39.10])

        line = 3.0
        superline = 10.0
        c1 = 'orange'
        c2 = 'royalblue'
        c3 = 'green'
        linestyle1 = '-'
        linestyle2 = '--'
                
        if i == "18":
            ax.plot(x_values18, y_values18, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "19":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "20":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "21":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "22":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "23":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "00":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "01":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "02":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "03":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "04":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "05":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "06":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "07":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)

        ax.plot(1,1,linestyle="--", color=c1, linewidth=5, label='Cell Tracks')
        ax.plot(1,1,linestyle="--", color=c2, linewidth=5, label =  "Severe")
        ax.plot(1,1,linestyle="--", color=c3, linewidth=5, label =  "Tornadic")
        ax.plot(1,1,linestyle="-", color='black', linewidth=10, label =  "Current Hour")

        #vmax = df1['highBound'][j]
        #vmin = df1['lowBound'][j]
        levels = range(int(df1['lowBound'][j]), int(df1['highBound'][j]), int(df1['cf_levels'][j]))
        #levels = np.array([int(df1['lowBound'][j]), int(df1['highBound'][j]), int(df1['cf_levels'][j])])
        #print(levels)

        def truncate_colormap(cmap, minval=0.0, maxval=1.0, n=20):
            new_cmap = colors.LinearSegmentedColormap.from_list(
                'trunc({n},{a:.2f},{b:.2f})'.format(n=cmap.name, a=minval, b=maxval),
                cmap(np.linspace(minval, maxval, n)))
            return new_cmap

        cmap_1 = plt.get_cmap('binary')
        cmap_2 = plt.get_cmap('Greys')
        cmap1 = truncate_colormap(cmap_1, 0, 0.5)
        cmap2 = truncate_colormap(cmap_2, 0.5, 1.0)

        cf = ax.contour(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap2) # Make a filled contour plot
        cf1 = ax.contourf(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap1) # Make a filled contour plot

        cbar = plt.colorbar(cf1, shrink=0.55, pad=0.01)
        cbar.ax.tick_params(labelsize=20)

        fig.set_facecolor('whitesmoke')
        plt.legend(loc='upper left', fontsize = 35,shadow=True)
        #fig.tight_layout()
        plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(df1['param'][j])+"_"+str(i)+"_"+str(j)+".png", bbox_inches='tight')
        #plt.show()
        plt.close(fig)
        plt.clf()
        
        print(df1['param'][j], i, j)
        j+=1
    #notify.send('figs for hour'+str(i)+' completed')

BRN_shear 18 0
mlBRN 18 1
muBRN 18 2
BRN_shear 19 0
mlBRN 19 1
muBRN 19 2
BRN_shear 20 0
mlBRN 20 1
muBRN 20 2
BRN_shear 21 0
mlBRN 21 1
muBRN 21 2
BRN_shear 22 0
mlBRN 22 1
muBRN 22 2
BRN_shear 23 0
mlBRN 23 1
muBRN 23 2
BRN_shear 00 0
mlBRN 00 1
muBRN 00 2
BRN_shear 01 0
mlBRN 01 1
muBRN 01 2
BRN_shear 02 0
mlBRN 02 1
muBRN 02 2
BRN_shear 03 0
mlBRN 03 1
muBRN 03 2
BRN_shear 04 0
mlBRN 04 1
muBRN 04 2
BRN_shear 05 0
mlBRN 05 1
muBRN 05 2
BRN_shear 06 0
mlBRN 06 1
muBRN 06 2
BRN_shear 07 0
mlBRN 07 1
muBRN 07 2


<Figure size 640x480 with 0 Axes>

In [ ]:
for i in hours:
    print(i)

In [1]:
import glob
import matplotlib.colors as colors

reader = shpreader.Reader(r"C:\Users\kyled\Desktop\Thesis GIS Data\County1010\countyl010g.shp")
counties = list(reader.geometries())
COUNTIES = cfeature.ShapelyFeature(counties, ccrs.PlateCarree())
proj = ccrs.PlateCarree()
#df1 = pd.read_csv(r"C:\Users\kyled\Desktop\mapPlots.csv")
df1 = pd.read_csv(r"C:\Users\kyled\Desktop\Round2.csv")

hours = ["18", "19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["01"]
#hours = ["19", "20", "21", "22", "23", "00", "01", "02", "03", "04", "05", "06", "07"]
#hours = ["18", "19", "20"]
#hours = ["21", "22", "23"]
#hours = ["00", "01", "02"]
#hours = ["04", "05", "06", "07"]
#hours = ["06", "07"]

for i in hours:
    folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\Round_2\_"+str(i)
    #folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(i)
    files = glob.glob(folder+'\*.csv')

    for j in range(0, len(files)):
    #for j in range(0, 11):
        df = pd.read_csv(files[j],header = None)
        df.fillna(0,inplace=True)
        data = df.to_numpy()
        #print(data)
        #print(files[j][41:], data.shape, np.amin(data), np.amax(data))
        if i == "18":
            day0 = "22"
        elif i == "19":
            day0 = "22"
        elif i == "20":
            day0 = "22"
        elif i == "21":
            day0 = "22"
        elif i == "22":
            day0 = "22"
        elif i == "23":
            day0 = "22"
        else:
            day0 = "23"

        title = str(day0)+" May 2019, "+str(i)+"z \n Observed Storm Tracks (by storm type) \n" + df1['param'][j]
        fig=plt.figure(figsize = (36,36), dpi=300, num=1, clear=True)
        #fig=plt.figure(figsize = (36,36), dpi=300, clear=True)
        ax = plt.axes(projection=ccrs.PlateCarree())
        #ax.set_title(title, fontsize=45, fontweight='bold')
        #ax.set_xlabel("test",size = 26)
        #ax.set_ylabel("test",size = 26,alpha=1.0)
        #ax.set_xlabel('lon')
        #ax.set_ylabel('lat')
        ax.set_xticks([-180,-120,-60,0,60,120,180])
        ax.set_yticks([-90,-60,-30,0,30,60,90])

        #ax.imshow(SFCP[0])
        ax.add_feature(cfeature.STATES.with_scale('50m'), linestyle='-', edgecolor='black', linewidth=1.5)
        ax.add_feature(COUNTIES, facecolor='none', edgecolor='black', linewidth=0.75)
        ax.set_extent([-100.73, -91.36, 32.52, 39.10])

        line = 3.0
        superline = 10.0
        c1 = 'orange'
        c2 = 'royalblue'
        c3 = 'green'
        linestyle1 = '-'
        linestyle2 = '--'

        if i == "18":
            ax.plot(x_values18, y_values18, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "19":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "20":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "21":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "22":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "23":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "00":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "01":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "02":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "03":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "04":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "05":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "06":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values07, y_values07, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
        elif i == "07":
            ax.plot(x_values18, y_values18, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values19, y_values19, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values20, y_values20, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values21, y_values21, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values22, y_values22, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values23, y_values23, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values00, y_values00, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values01, y_values01, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values02, y_values02, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values03, y_values03, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values04, y_values04, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values05, y_values05, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values06, y_values06, linestyle=linestyle2, color=c1, linewidth=line)
            ax.plot(x_values07, y_values07, linestyle=linestyle1, color=c1, linewidth=superline)
            ax.plot(x_values19_Severe, y_values19_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values20_Severe, y_values20_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values21_Severe, y_values21_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values22_Severe, y_values22_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values23_Severe, y_values23_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values00_Severe, y_values00_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values01_Severe, y_values01_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values02_Severe, y_values02_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values03_Severe, y_values03_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values04_Severe, y_values04_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values05_Severe, y_values05_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values06_Severe, y_values06_Severe, linestyle=linestyle2, color=c2, linewidth=line)
            ax.plot(x_values07_Severe, y_values07_Severe, linestyle=linestyle1, color=c2, linewidth=superline)
            ax.plot(x_values19_Tornado, y_values19_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values20_Tornado, y_values20_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values21_Tornado, y_values21_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values22_Tornado, y_values22_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values23_Tornado, y_values23_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values00_Tornado, y_values00_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values01_Tornado, y_values01_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values02_Tornado, y_values02_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values03_Tornado, y_values03_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values04_Tornado, y_values04_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values05_Tornado, y_values05_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values06_Tornado, y_values06_Tornado, linestyle=linestyle2, color=c3, linewidth=line)
            ax.plot(x_values07_Tornado, y_values07_Tornado, linestyle=linestyle1, color=c3, linewidth=superline)

        #ax.plot(1,1,linestyle="--", color=c1, linewidth=5, label='Cell Tracks')
        #ax.plot(1,1,linestyle="--", color=c2, linewidth=5, label =  ">120m life")
        #ax.plot(1,1,linestyle="--", color=c3, linewidth=5, label =  "Supercell")
        #ax.plot(1,1,linestyle="-", color='black', linewidth=10, label =  "Current Hour")

        #vmax = df1['highBound'][j]
        #vmin = df1['lowBound'][j]
        levels = np.arange(df1['lowBound'][j], df1['highBound'][j], df1['cf_levels'][j])
        #levels = np.arange(-1, 2.1, 0.2)
        #levels = np.array([int(df1['lowBound'][j]), int(df1['highBound'][j]), int(df1['cf_levels'][j])])
        #print(levels)

        def truncate_colormap(cmap, minval=0.0, maxval=1.0, n=20):
            new_cmap = colors.LinearSegmentedColormap.from_list(
                'trunc({n},{a:.2f},{b:.2f})'.format(n=cmap.name, a=minval, b=maxval),
                cmap(np.linspace(minval, maxval, n)))
            return new_cmap

        #cmap_1 = plt.get_cmap('binary')
        cmap_1 = plt.get_cmap('gray')
        cmap_2 = plt.get_cmap('Greys')
        #cmap1 = truncate_colormap(cmap_1, 0, 0.5)
        cmap1 = truncate_colormap(cmap_1, 0.5, 1.0)
        cmap2 = truncate_colormap(cmap_2, 0.5, 1.0)

        cf = ax.contour(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap2) # Make a filled contour plot
        cf1 = ax.contourf(trlons[107:160, 210:270], trlats[107:160, 210:270], data, levels = levels, cmap=cmap1) # Make a filled contour plot

        #cbar = plt.colorbar(cf1, shrink=0.55, pad=0.01)
        #cbar.ax.tick_params(labelsize=20)

        fig.set_facecolor('whitesmoke')
        #plt.legend(loc='upper left', fontsize = 35,shadow=True)
        #fig.tight_layout()
        plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(df1['param'][j])+"_"+str(i)+".png", bbox_inches='tight', dpi=300)
        #plt.show()
        #plt.close(fig)
        #fig.clear()
        #plt.clf()

        print(df1['param'][j], i, j)
        j+=1
        #notify.send('figs for hour'+str(i)+' completed')

NameError: name 'shpreader' is not defined

In [ ]:
#hours = ["18", "19", "20", "21", "22", "23"]
#hours = ["01"]
#for i in hours:
    folder = r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(i)
    df = pd.read_csv(r'C:\Users\kyled\Desktop\RAPout_Arrays\_'+str(i)+'\MCS_maint_prob_'+str(i)+'.csv',header = None)
    df.fillna(0,inplace=True)
    data = df.to_numpy()
    data1 = data*100

#    df1 = pd.read_csv(r'C:\Users\kyled\Desktop\RAPout_Arrays\_'+str(i)+'\MU_HLFC_'+str(i)+'.csv',header = None)
#    df1.fillna(0,inplace=True)
#    data2 = df1.to_numpy()
#    data3 = data2/1000

#    np.savetxt("C:/Users/KyleD/Desktop/RAPout_Arrays/_"+str(i)+"/MCS_maint_prob_"+str(i)+".csv",data1,delimiter=",",fmt='%s')
#    np.savetxt("C:/Users/KyleD/Desktop/RAPout_Arrays/_"+str(i)+"/MU_HLFC_"+str(i)+".csv",data3,delimiter=",",fmt='%s')

In [ ]:
print(cbar.shape)

In [ ]:
fig = plt.figure(figsize=(16, 9), dpi=300, num=1, clear=True)
    #fig = plt.subplots(nrows=3, ncols=4, figsize=(20, 13.333), subplot_kw={'xticks': [], 'yticks': []}, gridspec_kw = {'wspace':0.001, 'hspace':0.000001})

figsize = 0.42

fig.text(0.05, 1.27, str(df1['param'][j]), size=48, fontweight = "bold")



ax1 = fig.add_axes([0, 0.83, figsize, figsize]) #top left
ax1.set_xticks([])
ax1.set_yticks([])
fig.text(0.30, 0.85, "18z", size=36, fontweight = "bold")

ax2 = fig.add_axes([0.334, 0.83, figsize, figsize]) #top left
ax2.set_xticks([])
ax2.set_yticks([])
fig.text(0.635, 0.85, "19z", size=36, fontweight = "bold")

ax3 = fig.add_axes([0.668, 0.83, figsize, figsize]) #top right
ax3.set_xticks([])
ax3.set_yticks([])
fig.text(0.97, 0.85, "20z", size=36, fontweight = "bold")

ax4 = fig.add_axes([1.001, 0.83, figsize, figsize]) #top right
ax4.set_xticks([])
ax4.set_yticks([])
fig.text(1.305, 0.85, "21z", size=36, fontweight = "bold")

ax5 = fig.add_axes([0, 0.415, figsize, figsize]) #bottom right
ax5.set_xticks([])
ax5.set_yticks([])
fig.text(0.30, 0.435, "22z", size=36, fontweight = "bold")

ax6 = fig.add_axes([0.334, 0.415, figsize, figsize]) #bottom right
ax6.set_xticks([])
ax6.set_yticks([])
fig.text(0.635, 0.435, "23z", size=36, fontweight = "bold")

ax7 = fig.add_axes([0.668, 0.415, figsize, figsize]) #bottom right
ax7.set_xticks([])
ax7.set_yticks([])
fig.text(0.97, 0.435, "00z", size=36, fontweight = "bold")

ax8 = fig.add_axes([1.001, 0.415, figsize, figsize]) #bottom right
ax8.set_xticks([])
ax8.set_yticks([])
fig.text(1.305, 0.435, "01z", size=36, fontweight = "bold")

ax9 = fig.add_axes([0, 0, figsize, figsize]) #bottom right
ax9.set_xticks([])
ax9.set_yticks([])
fig.text(0.30, 0.02, "02z", size=36, fontweight = "bold")

ax10 = fig.add_axes([0.334, 0, figsize, figsize]) #bottom right
ax10.set_xticks([])
ax10.set_yticks([])
fig.text(0.635, 0.02, "03z", size=36, fontweight = "bold")

ax11 = fig.add_axes([0.668, 0, figsize, figsize]) #bottom right
ax11.set_xticks([])
ax11.set_yticks([])
fig.text(0.97, 0.02, "04z", size=36, fontweight = "bold")

ax12 = fig.add_axes([1.001, 0, figsize, figsize]) #bottom right
ax12.set_xticks([])
ax12.set_yticks([])
fig.text(1.305, 0.02, "05z", size=36, fontweight = "bold")

ax1.imshow(img01)
ax2.imshow(img02)
ax3.imshow(img03)
ax4.imshow(img04)
ax5.imshow(img05)
ax6.imshow(img06)
ax7.imshow(img07)
ax8.imshow(img08)
ax9.imshow(img09)
ax10.imshow(img10)
ax11.imshow(img11)
ax12.imshow(img12)

fig.set_facecolor('whitesmoke')

#ax0 = fig.add_axes([0.78, 0, 1.25, 1.25]) #bottom right
ax0 = fig.add_axes([0.79, 0, 1.25, 1.25]) #bottom right
ax0.set_xticks([])
ax0.set_yticks([])
cbar = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/SVRtor/'+str(df1['param'][j])+'\_'+str(df1['param'][j])+'_18.png')
ax0.imshow(cbar[175:1300,1700:,:])

ax13 = fig.add_axes([0.63, 0.89, 0.80, 0.80]) #bottom right
ax13.set_xticks([])
ax13.set_yticks([])
leg = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/SVRtorBar.png')
#ax13.imshow(cbar[175:1300,1700:1808,:])
ax13.imshow(leg)

plt.show()

In [4]:
import matplotlib.image as mpimg
import pandas as pd
#df1 = pd.read_csv(r"C:\Users\kyled\Desktop\mapPlots.csv")
df1 = pd.read_csv(r"C:\Users\kyled\Desktop\Round2.csv")

for j in range(0, len(df1)):

    img01 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_18.png')
    img02 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_19.png')
    img03 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_20.png')
    img04 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_21.png')
    img05 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_22.png')
    img06 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_23.png')
    img07 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_00.png')
    img08 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_01.png')
    img09 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_02.png')
    img10 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_03.png')
    img11 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_04.png')
    img12 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][j])+'_05.png')

    fig = plt.figure(figsize=(16, 9), dpi=300, num=1, clear=True)
    #fig = plt.subplots(nrows=3, ncols=4, figsize=(20, 13.333), subplot_kw={'xticks': [], 'yticks': []}, gridspec_kw = {'wspace':0.001, 'hspace':0.000001})

    figsize = 0.42

    fig.text(0.05, 1.27, str(df1['param'][j]), size=48, fontweight = "bold")

    ax1 = fig.add_axes([0, 0.83, figsize, figsize]) #top left
    ax1.set_xticks([])
    ax1.set_yticks([])
    fig.text(0.30, 0.85, "18z", size=36, fontweight = "bold")

    ax2 = fig.add_axes([0.334, 0.83, figsize, figsize]) #top left
    ax2.set_xticks([])
    ax2.set_yticks([])
    fig.text(0.635, 0.85, "19z", size=36, fontweight = "bold")

    ax3 = fig.add_axes([0.668, 0.83, figsize, figsize]) #top right
    ax3.set_xticks([])
    ax3.set_yticks([])
    fig.text(0.97, 0.85, "20z", size=36, fontweight = "bold")

    ax4 = fig.add_axes([1.001, 0.83, figsize, figsize]) #top right
    ax4.set_xticks([])
    ax4.set_yticks([])
    fig.text(1.305, 0.85, "21z", size=36, fontweight = "bold")

    ax5 = fig.add_axes([0, 0.415, figsize, figsize]) #bottom right
    ax5.set_xticks([])
    ax5.set_yticks([])
    fig.text(0.30, 0.435, "22z", size=36, fontweight = "bold")

    ax6 = fig.add_axes([0.334, 0.415, figsize, figsize]) #bottom right
    ax6.set_xticks([])
    ax6.set_yticks([])
    fig.text(0.635, 0.435, "23z", size=36, fontweight = "bold")

    ax7 = fig.add_axes([0.668, 0.415, figsize, figsize]) #bottom right
    ax7.set_xticks([])
    ax7.set_yticks([])
    fig.text(0.97, 0.435, "00z", size=36, fontweight = "bold")

    ax8 = fig.add_axes([1.001, 0.415, figsize, figsize]) #bottom right
    ax8.set_xticks([])
    ax8.set_yticks([])
    fig.text(1.305, 0.435, "01z", size=36, fontweight = "bold")

    ax9 = fig.add_axes([0, 0, figsize, figsize]) #bottom right
    ax9.set_xticks([])
    ax9.set_yticks([])
    fig.text(0.30, 0.02, "02z", size=36, fontweight = "bold")

    ax10 = fig.add_axes([0.334, 0, figsize, figsize]) #bottom right
    ax10.set_xticks([])
    ax10.set_yticks([])
    fig.text(0.635, 0.02, "03z", size=36, fontweight = "bold")

    ax11 = fig.add_axes([0.668, 0, figsize, figsize]) #bottom right
    ax11.set_xticks([])
    ax11.set_yticks([])
    fig.text(0.97, 0.02, "04z", size=36, fontweight = "bold")

    ax12 = fig.add_axes([1.001, 0, figsize, figsize]) #bottom right
    ax12.set_xticks([])
    ax12.set_yticks([])
    fig.text(1.305, 0.02, "05z", size=36, fontweight = "bold")

    ax1.imshow(img01)
    ax2.imshow(img02)
    ax3.imshow(img03)
    ax4.imshow(img04)
    ax5.imshow(img05)
    ax6.imshow(img06)
    ax7.imshow(img07)
    ax8.imshow(img08)
    ax9.imshow(img09)
    ax10.imshow(img10)
    ax11.imshow(img11)
    ax12.imshow(img12)
    
    #ax0 = fig.add_axes([0.78, 0, 1.25, 1.25]) #bottom right
    ax0 = fig.add_axes([0.79, 0, 1.25, 1.25]) #bottom right
    ax0.set_xticks([])
    ax0.set_yticks([])
    cbar = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/120supercell/'+str(df1['param'][j])+'\_'+str(df1['param'][j])+'_18.png')
    #ax0.imshow(cbar[175:1300,1700:,:])
    ax0.imshow(cbar[800:5500,7100:,:])

    ax13 = fig.add_axes([0.63, 0.89, 0.80, 0.80]) #bottom right
    ax13.set_xticks([])
    ax13.set_yticks([])
    leg = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/120supercellBar.png')
    #ax13.imshow(cbar[175:1300,1700:1808,:])
    ax13.imshow(leg)

    fig.set_facecolor('whitesmoke')
    #fig.tight_layout()
    
    #plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\120supercells_MULTIPANEL\_"+str(df1['param'][j])+"_120supercell.png", bbox_inches='tight', dpi=300)
    plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(df1['param'][j])+"_120supercell.png", bbox_inches='tight', dpi=300)
    print(j)

    #fig.text(0.10, 1.27, "mlCIN", size=48, fontweight = "bold")
    #plt.show()

0
1
2
Error in callback <function flush_figures at 0x00000184F68DE430> (for post_execute):


KeyboardInterrupt: 

In [15]:
print(df1['param'][0])

BRN_shear


In [4]:
import matplotlib.image as mpimg
import pandas as pd
matplotlib.use('Agg')
df1 = pd.read_csv(r"C:\Users\kyled\Desktop\CSV_Plot_Lists\mapPlots.csv")
#df1 = pd.read_csv(r"C:\Users\kyled\Desktop\Round2.csv")

#for j in range(2, len(df1)):
img01 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_18.png')
img02 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_19.png')
img03 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_20.png')
img04 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_21.png')
img05 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_22.png')
img06 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_23.png')
img07 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_00.png')
img08 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_01.png')
img09 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_02.png')
img10 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_03.png')
img11 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_04.png')
img12 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\120supercellFull\_'+str(df1['param'][107])+'_05.png')

fig = plt.figure(figsize=(16, 9), num=1, clear=True)
#fig = plt.figure(figsize=(16, 9), dpi=300, num=1, clear=True)
#fig = plt.subplots(nrows=3, ncols=4, figsize=(20, 13.333), subplot_kw={'xticks': [], 'yticks': []}, gridspec_kw = {'wspace':0.001, 'hspace':0.000001})

figsize = 0.42

fig.text(0.07, 1.69, str(df1['param'][107]), size=36, fontweight = "bold")

ax1 = fig.add_axes([0, 1.25, figsize, figsize]) #top left
ax1.set_xticks([])
ax1.set_yticks([])
fig.text(0.05, 1.60, "18z", size=24, fontweight = "bold")

ax2 = fig.add_axes([0.334, 1.25, figsize, figsize]) #top left
ax2.set_xticks([])
ax2.set_yticks([])
fig.text(0.385, 1.60, "19z", size=24, fontweight = "bold")

ax3 = fig.add_axes([0.668, 1.25, figsize, figsize]) #top right
ax3.set_xticks([])
ax3.set_yticks([])
fig.text(0.72, 1.60, "20z", size=24, fontweight = "bold")

ax4 = fig.add_axes([0, 0.833, figsize, figsize]) #bottom right
#ax4 = fig.add_axes([1.001, 0.83, figsize, figsize]) #top right
ax4.set_xticks([])
ax4.set_yticks([])
fig.text(0.05, 1.183, "21z", size=24, fontweight = "bold")
#fig.text(1.305, 0.85, "21z", size=24, fontweight = "bold")

ax5 = fig.add_axes([0.334, 0.833, figsize, figsize]) #bottom right
#ax5 = fig.add_axes([0, 0.415, figsize, figsize]) #bottom right
ax5.set_xticks([])
ax5.set_yticks([])
fig.text(0.385, 1.183, "22z", size=24, fontweight = "bold")

ax6 = fig.add_axes([0.668, 0.833, figsize, figsize]) #bottom right
ax6.set_xticks([])
ax6.set_yticks([])
fig.text(0.72, 1.183, "23z", size=24, fontweight = "bold")

ax7 = fig.add_axes([0, 0.415, figsize, figsize]) #bottom right
ax7.set_xticks([])
ax7.set_yticks([])
fig.text(0.05, 0.766, "00z", size=24, fontweight = "bold")

ax8 = fig.add_axes([0.334, 0.415, figsize, figsize]) #bottom right
ax8.set_xticks([])
ax8.set_yticks([])
fig.text(0.385, 0.766, "01z", size=24, fontweight = "bold")

ax9 = fig.add_axes([0.668, 0.415, figsize, figsize]) #bottom right
ax9.set_xticks([])
ax9.set_yticks([])
fig.text(0.72, 0.766, "02z", size=24, fontweight = "bold")

ax10 = fig.add_axes([0, 0, figsize, figsize]) #bottom right
ax10.set_xticks([])
ax10.set_yticks([])
fig.text(0.05, 0.349, "03z", size=24, fontweight = "bold")

ax11 = fig.add_axes([0.334, 0, figsize, figsize]) #bottom right
ax11.set_xticks([])
ax11.set_yticks([])
fig.text(0.385, 0.349, "04z", size=24, fontweight = "bold")

ax12 = fig.add_axes([0.668, 0, figsize, figsize]) #bottom right
ax12.set_xticks([])
ax12.set_yticks([])
fig.text(0.72, 0.349, "05z", size=24, fontweight = "bold")

ax1.imshow(img01[200:5800,400:8200,:])
ax2.imshow(img02[200:5800,400:8200,:])
ax3.imshow(img03[200:5800,400:8200,:])
ax4.imshow(img04[200:5800,400:8200,:])
ax5.imshow(img05[200:5800,400:8200,:])
ax6.imshow(img06[200:5800,400:8200,:])
ax7.imshow(img07[200:5800,400:8200,:])
ax8.imshow(img08[200:5800,400:8200,:])
ax9.imshow(img09[200:5800,400:8200,:])
ax10.imshow(img10[200:5800,400:8200,:])
ax11.imshow(img11[200:5800,400:8200,:])
ax12.imshow(img12[200:5800,400:8200,:])

#ax1.imshow(img01)
#ax2.imshow(img02)
#ax3.imshow(img03)
#ax4.imshow(img04)
#ax5.imshow(img05)
#ax6.imshow(img06)
#ax7.imshow(img07)
#ax8.imshow(img08)
#ax9.imshow(img09)
#ax10.imshow(img10)
#ax11.imshow(img11)
#ax12.imshow(img12)

#ax0 = fig.add_axes([0.78, 0, 1.25, 1.25]) #bottom right
ax0 = fig.add_axes([0.51, 0.35, 1.0, 1.0]) #bottom right
ax0.set_xticks([])
ax0.set_yticks([])
cbar = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/120supercell/'+str(df1['param'][107])+'\_'+str(df1['param'][107])+'_18.png')
ax0.imshow(cbar[800:5500,7100:,:])

ax13 = fig.add_axes([0.15, -0.41, 0.75, 0.75]) #bottom right
ax13.set_xticks([])
ax13.set_yticks([])
leg = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/120supercellBar.png')
#ax13.imshow(cbar[175:1300,1700:1808,:])
ax13.imshow(leg)

fig.set_facecolor('whitesmoke')
#fig.tight_layout()
#plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\__NEW_MP\_"+str(df1['param'][107])+"_120supercell.png", bbox_inches='tight')

plt.switch_backend('Agg')
plt.cla()
plt.clf()
plt.close('all')
#plt.savefig(r"C:\Users\kyled\Desktop\TestNEW.png", bbox_inches='tight')

#plt.show()
print("j")

#plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\_"+str(df1['param'][107])+"_120supercell.png", bbox_inches='tight', dpi=300)
#print(j)

KeyboardInterrupt: 

In [4]:
print(img01.shape)
ax0.imshow(cbar)


print(img02.shape)
print(img03.shape)
print(img04.shape)

(5937, 8430, 4)
(5937, 8430, 4)
(5937, 8430, 4)
(5937, 8430, 4)


In [ ]:
fig = plt.figure(figsize=(16, 9), dpi=300, num=1, clear=True)

ax0 = fig.add_axes([0.79, 0, 1.25, 1.25]) #bottom right
ax0.set_xticks([])
ax0.set_yticks([])
cbar = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/120supercell/'+str(df1['param'][0])+'\_'+str(df1['param'][0])+'_18.png')
print(cbar.shape)
#ax0.imshow(cbar)
ax0.imshow(cbar[800:5500,7100:,:])

plt.show()

In [6]:
import matplotlib.image as mpimg
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

df1 = pd.read_csv(r"C:\Users\kyled\Desktop\mapPlots.csv")

#for j in range(57, len(df1)):

#fig = plt.figure(figsize=(16, 9), dpi=300, num=1, clear=True)
fig = plt.figure(figsize=(16, 9), dpi=300)
#fig = plt.subplots(nrows=3, ncols=4, figsize=(20, 13.333), subplot_kw={'xticks': [], 'yticks': []}, gridspec_kw = {'wspace':0.001, 'hspace':0.000001})

img01 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_18.png')
img02 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_19.png')
img03 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_20.png')
img04 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_21.png')
img05 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_22.png')
img06 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_23.png')
img07 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_00.png')
img08 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_01.png')
img09 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_02.png')
img10 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_03.png')
img11 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_04.png')
img12 = mpimg.imread(r'C:\Users\kyled\Desktop\RAPout_Arrays\SVRtorFull\_'+str(df1['param'][31])+'_05.png')   

figsize = 0.42

fig.text(0.05, 1.27, str(df1['param'][31]), size=48, fontweight = "bold")

ax1 = fig.add_axes([0, 0.83, figsize, figsize]) #top left
ax1.set_xticks([])
ax1.set_yticks([])
fig.text(0.30, 0.85, "18z", size=36, fontweight = "bold")

ax2 = fig.add_axes([0.334, 0.83, figsize, figsize]) #top left
ax2.set_xticks([])
ax2.set_yticks([])
fig.text(0.635, 0.85, "19z", size=36, fontweight = "bold")

ax3 = fig.add_axes([0.668, 0.83, figsize, figsize]) #top right
ax3.set_xticks([])
ax3.set_yticks([])
fig.text(0.97, 0.85, "20z", size=36, fontweight = "bold")

ax4 = fig.add_axes([1.001, 0.83, figsize, figsize]) #top right
ax4.set_xticks([])
ax4.set_yticks([])
fig.text(1.305, 0.85, "21z", size=36, fontweight = "bold")

ax5 = fig.add_axes([0, 0.415, figsize, figsize]) #bottom right
ax5.set_xticks([])
ax5.set_yticks([])
fig.text(0.30, 0.435, "22z", size=36, fontweight = "bold")

ax6 = fig.add_axes([0.334, 0.415, figsize, figsize]) #bottom right
ax6.set_xticks([])
ax6.set_yticks([])
fig.text(0.635, 0.435, "23z", size=36, fontweight = "bold")

ax7 = fig.add_axes([0.668, 0.415, figsize, figsize]) #bottom right
ax7.set_xticks([])
ax7.set_yticks([])
fig.text(0.97, 0.435, "00z", size=36, fontweight = "bold")

ax8 = fig.add_axes([1.001, 0.415, figsize, figsize]) #bottom right
ax8.set_xticks([])
ax8.set_yticks([])
fig.text(1.305, 0.435, "01z", size=36, fontweight = "bold")

ax9 = fig.add_axes([0, 0, figsize, figsize]) #bottom right
ax9.set_xticks([])
ax9.set_yticks([])
fig.text(0.30, 0.02, "02z", size=36, fontweight = "bold")

ax10 = fig.add_axes([0.334, 0, figsize, figsize]) #bottom right
ax10.set_xticks([])
ax10.set_yticks([])
fig.text(0.635, 0.02, "03z", size=36, fontweight = "bold")

ax11 = fig.add_axes([0.668, 0, figsize, figsize]) #bottom right
ax11.set_xticks([])
ax11.set_yticks([])
fig.text(0.97, 0.02, "04z", size=36, fontweight = "bold")

ax12 = fig.add_axes([1.001, 0, figsize, figsize]) #bottom right
ax12.set_xticks([])
ax12.set_yticks([])
fig.text(1.305, 0.02, "05z", size=36, fontweight = "bold")

ax1.imshow(img01)
ax2.imshow(img02)
ax3.imshow(img03)
ax4.imshow(img04)
ax5.imshow(img05)
ax6.imshow(img06)
ax7.imshow(img07)
ax8.imshow(img08)
ax9.imshow(img09)
ax10.imshow(img10)
ax11.imshow(img11)
ax12.imshow(img12)

#ax0 = fig.add_axes([0.78, 0, 1.25, 1.25]) #bottom right
ax0 = fig.add_axes([0.79, 0, 1.25, 1.25]) #bottom right
ax0.set_xticks([])
ax0.set_yticks([])
cbar = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/SVRtor/'+str(df1['param'][31])+'/_'+str(df1['param'][31])+'_18.png')
#ax0.imshow(cbar[175:1300,1700:,:])
ax0.imshow(cbar[800:5500,7100:,:])

ax13 = fig.add_axes([0.63, 0.89, 0.80, 0.80]) #bottom right
ax13.set_xticks([])
ax13.set_yticks([])
leg = mpimg.imread('C:/Users/kyled/Desktop/RAPout_Arrays/SVRtorBar.png')
#ax13.imshow(cbar[175:1300,1700:1808,:])
ax13.imshow(leg)

fig.set_facecolor('whitesmoke')
#fig.tight_layout()

plt.savefig(r"C:\Users\kyled\Desktop\RAPout_Arrays\SVRtor_MULTIPANEL\_"+str(df1['param'][31])+"_SVRtor.png", bbox_inches='tight', dpi=300)
plt.cla()
plt.clf()
print(df1['param'][31])

#fig.text(0.10, 1.27, "mlCIN", size=48, fontweight = "bold")
plt.show()

mlCIN


<Figure size 4800x2700 with 0 Axes>